# INM433 Visual Analytics: Lab08

# Spatially varying explanations behind Brexit voting

*Originally written in R by Roger Beecham and Aidan Slingsby in 2016. Adapted to Python by Rafael Henkin in 2019 and further adapted by Aidan in 2020 and by Johannes in 2021*

In this practical session you’ll be doing some visual analytics in Python, using libraries that you should be now familiar with and a couple of new ones.

The basic code is provided. This practical focussed on the reasoning and interepretation of graphical output given research questions. The practical will cover a topic that is still in the news: the UK’s referendum vote on membership of the EU. The vote was a few years ago, but several issues that arose still haven't been fully resolved.

## Introduction

The narrow vote in favour of Leave was unexpected. You've probably heard commentators remark on the underlying causes for why people voted as they did. These pronouncements have often been made based on the very obvious [geographic differences](http://www.bbc.co.uk/news/uk-politics-36616028) in voting preference. A familiar caricature in the media is of Leave voting being a symptom of "blue collar disaffection" and Remain voting of "liberal values and (relative) affluence". But is this borne out in the data?

Our research questions are:

 * Can we account for geographical differences in the referendum results using demographic data?
 * Can we explain the referendum results in terms of the characteristics of the population?
 * Do these explanations vary geographically?

Here we'll take a single continuous outcome variable -- the share of vote in favour of Leave in each GB Local Authority (LA) -- and study the extent to which key sociology-economic variables from the 2011 Census might help explain this outcome. Towards the end, we will try to use geographically-weighted statistics to investigate how the relationships in candidate explanations vary geographically.  

Important to note that we're *not looking at individual behaviour* here. We're looking at data *aggregated at Local Authority (LA) level* and this must be kept in mind. 

For this practical, one *motivation* is that although the overall Remain:Leave vote was about 48:52, this ratio was certainty *not uniformly spread*. Every LA in Scotland voted to Remain, for example, and so too did inner London and parts of Northern Ireland. Motivating this study is to better *understand* what might drive these differences.

We could come up with *research questions* such as:

 * Did Scotland vote differently from the rest of the UK given its population structure? (Is Scotland different?)
 * Are the factors that drove the vote the same everywhere in the Great Britain?

This practical is about the *analytic tasks* chosen to answer such questions and the *visual analytics methods* that can be employed to carry out these tasks. As ever, a particular set of approaches is used here. But there are many other approaches, techniques and things to investigate.

The following analytical tasks will help address these research questions:

 * To *describe* how the referedum results vary geographically and how they *relate* to demographic variables
 * To *choose* demographic variables for which there are is a theoretical and a data-driven reason for using them
 * To build *models* to explore the population characteristics that appear to *drive* the referendum results and to assess their *quality*
 * To build *geographically-weighted* models to explore whether these relationships vary geographically
 * To identify *parts of the country* with similar relationships between demographics and voting outcome

## Python preparation

In addition to familiar libraries such as numpy and pandas, we will make heavy use of [Altair](https://altair-viz.github.io/index.html) as our visualisation library of choice. There are of course other options, such as Matplotlib, Seaborn and Bokeh. Our main reason for using Altair is the fact that it produces, out-of-the-box, SVG graphics and JSON specifications of Vega-Lite charts, which are portable web-based graphics. Altair is essentially a Python API of Vega-Lite, which is part of the [Vega](https://vega.github.io/) family of visualisation grammars (think ggplot if you know R). These are state-of-the-art languages for *declaring* interactive graphics by mapping data variables to visual variables.

_Libraries below can be installed with the Anaconda navigator or_:  

    conda install libraryname      
    
_Sometimes you might need to install from the conda-forge channel:_  
    
    conda install -c conda-forge libraryname
_Sometimes you need to install from pip_:

    pip install libraryname

_You might also need to install dependencies such as Vega_:
    
    conda install -c conda-forge Vega
    
Libraries we use in this practical (besides Altair):
- [gepandas](https://geopandas.org/en/stable/getting_started/install.html) (+dependencies)
- [statsmodels](https://www.statsmodels.org/stable/install.html)
- [mgwr](https://mgwr.readthedocs.io/en/latest/index.html)
- [sklearn](https://scikit-learn.org/stable/)


### Importing necessary libraries

In [1]:
import pandas as pd
import numpy as np
import geopandas as gpd # More info on how to install geopandas https://geopandas.org/en/stable/getting_started/install.html
import altair as alt
import statsmodels.formula.api as smf
from statsmodels.stats.outliers_influence import variance_inflation_factor
from IPython.display import Markdown, display
from mgwr.gwr import GWR, MGWR
from mgwr.diagnostics import corr
from itertools import combinations as combo
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import AgglomerativeClustering
from sklearn.metrics import silhouette_score,silhouette_samples

### Loading the data

Next load the results data (the outcome variable), the Census 2011 data that you'll use as explanatory variables and [shapefiles](https://en.wikipedia.org/wiki/Shapefile) containing details of LA boundaries for mapping. Note that referendum results are available only at local authority level -- so we will use Census 2011 variables that are aggregated to this resolution.

The code below results in:

 * a DataFrame ("census_data") where rows are LAs and columns are Census variables and LA information (such as the Region they are part of)
 * a DataFrame ("referendum_data") where rows are LAs and columns describe voting behavior in the Referendum 

In [2]:
pd.set_option('display.max_columns', None)

In [3]:
referendum_data = pd.read_csv("data/referendum_data.csv")
census_data = pd.read_csv("data/2011_census_oa.csv")
lookup = pd.read_csv("data/oa_la_lookup.csv")

In [4]:
referendum_data.head(3)

Region_Code Region  Area_Code             Area  Electorate  Turnout  \
0   E12000006   East  E06000031     Peterborough      120892   0.7235   
1   E12000006   East  E06000032            Luton      127612   0.6631   
2   E12000006   East  E06000033  Southend-on-Sea      128856   0.7290   

   Valid_Votes   Leave  
0        87392  0.6089  
1        84481  0.5655  
2        93870  0.5808

In [5]:
census_data.head(3)

OA  Total_Population  Total_Households  \
0  E00000001               194                99   
1  E00000003               250               112   
2  E00000005               367               217   

   Total_Population_16_and_over  Total_Population_16_to_74  \
0                           173                        148   
1                           218                        199   
2                           337                        304   

   Total_Employment_16_to_74  Total_Population_in_Households_16_and_over  \
0                        102                                         173   
1                        147                                         218   
2                        241                                         337   

   Age_0_to_4  Age_5_to_9  Age_10_to_14  Age_15_to_19  Age_20_to_24  \
0          11           3             5             8             3   
1          14          12             5             5            10   
2          10          12             7             2            14   

   Age_25_to_29  Age_30_to_44  Age_45_to_59  Age_60_to_64  Age_65_to_74  \
0            14            30            49            20            26   
1            15            59            70            23            18   
2            37            93            96            30            33   

   Age_75_to_84  Age_85_to_89  Age_90_and_over  White_British_and_Irish  \
0            20             3                2                      157   
1            16             2                1                      179   
2            28             4                1                      268   

   White_Other_White  Mixed_or_multiple_ethnic_group  \
0                 18                              10   
1                 27                               9   
2                 53                              12   

   Asian_or_Asian_British_Indian  Asian_or_Asian_British_Pakistani  \
0                              2                                 0   
1                             17                                 0   
2                              9                                 1   

   Asian_or_Asian_British_Bangladeshi  Asian_or_Asian_British_Chinese  \
0                                   0                               4   
1                                   3                               3   
2                                   0                              10   

   Asian_or_Asian_British_Other_Asian  \
0                                   0   
1                                   3   
2                                   5   

   Black_or_African_or_Caribbean_or_Black_British_African  \
0                                                  0        
1                                                  3        
2                                                  4        

   Arab_or_Other_Ethnic_Groups  Christian  Other_religion  No_religion  \
0                            3         82               5           87   
1                            6        104              34           96   
2                            5        167              22          144   

   Religion_not_stated  \
0                   20   
1                   16   
2                   34   

   Main_language_is_English_or_Main_language_not_English__Can_speak_English_very_well  \
0                                                185                                    
1                                                233                                    
2                                                360                                    

   Main_language_is_not_English__Can_speak_English_well  \
0                                                  1      
1                                                  7      
2                                                  3      

   Main_language_is_not_English__Cannot_speak_English_well  \
0                                                  0         
1                              

In [6]:
lookup.head(3)

OA   LATITUDE  LONGITUDE LOCAL_AUTHORITY_CODE LOCAL_AUTHORITY_NAME  \
0  E00000001  51.520271  -0.095011            E09000001       City of London   
1  E00000003  51.519888  -0.096852            E09000001       City of London   
2  E00000005  51.519031  -0.096239            E09000001       City of London   

  REGION_OR_COUNTRY_CODE REGION_OR_COUNTRY_NAME  POPULATION  
0              E12000007                 London         194  
1              E12000007                 London         250  
2              E12000007                 London         367

In [7]:
# merge lookup to census data to bring the LOCAL_AUTHORITY_CODE fro grouping
census_data = pd.merge(census_data, lookup);

In [8]:
census_data.head(3)

OA  Total_Population  Total_Households  \
0  E00000001               194                99   
1  E00000003               250               112   
2  E00000005               367               217   

   Total_Population_16_and_over  Total_Population_16_to_74  \
0                           173                        148   
1                           218                        199   
2                           337                        304   

   Total_Employment_16_to_74  Total_Population_in_Households_16_and_over  \
0                        102                                         173   
1                        147                                         218   
2                        241                                         337   

   Age_0_to_4  Age_5_to_9  Age_10_to_14  Age_15_to_19  Age_20_to_24  \
0          11           3             5             8             3   
1          14          12             5             5            10   
2          10          12             7             2            14   

   Age_25_to_29  Age_30_to_44  Age_45_to_59  Age_60_to_64  Age_65_to_74  \
0            14            30            49            20            26   
1            15            59            70            23            18   
2            37            93            96            30            33   

   Age_75_to_84  Age_85_to_89  Age_90_and_over  White_British_and_Irish  \
0            20             3                2                      157   
1            16             2                1                      179   
2            28             4                1                      268   

   White_Other_White  Mixed_or_multiple_ethnic_group  \
0                 18                              10   
1                 27                               9   
2                 53                              12   

   Asian_or_Asian_British_Indian  Asian_or_Asian_British_Pakistani  \
0                              2                                 0   
1                             17                                 0   
2                              9                                 1   

   Asian_or_Asian_British_Bangladeshi  Asian_or_Asian_British_Chinese  \
0                                   0                               4   
1                                   3                               3   
2                                   0                              10   

   Asian_or_Asian_British_Other_Asian  \
0                                   0   
1                                   3   
2                                   5   

   Black_or_African_or_Caribbean_or_Black_British_African  \
0                                                  0        
1                                                  3        
2                                                  4        

   Arab_or_Other_Ethnic_Groups  Christian  Other_religion  No_religion  \
0                            3         82               5           87   
1                            6        104              34           96   
2                            5        167              22          144   

   Religion_not_stated  \
0                   20   
1                   16   
2                   34   

   Main_language_is_English_or_Main_language_not_English__Can_speak_English_very_well  \
0                                                185                                    
1                                                233                                    
2                                                360                                    

   Main_language_is_not_English__Can_speak_English_well  \
0                                                  1      
1                                                  7      
2                                                  3      

   Main_language_is_not_English__Cannot_speak_English_well  \
0                                                  0         
1                              

We then aggregate the data and compute some statistical summaries that might be relevant. We use iloc to keep only the variables we want to use in our analysis.

In [9]:
grouped = census_data.groupby('LOCAL_AUTHORITY_CODE').sum();

In [10]:
grouped.head(3)

Total_Population  Total_Households  \
LOCAL_AUTHORITY_CODE                                       
E06000001                        92028             40434   
E06000002                       138412             57203   
E06000003                       135177             59605   

                      Total_Population_16_and_over  Total_Population_16_to_74  \
LOCAL_AUTHORITY_CODE                                                            
E06000001                                    74228                      66804   
E06000002                                   110409                     100551   
E06000003                                   111011                      99177   

                      Total_Employment_16_to_74  \
LOCAL_AUTHORITY_CODE                              
E06000001                                 37767   
E06000002                                 54547   
E06000003                                 56354   

                      Total_Population_in_Households_16_and_over  Age_0_to_4  \
LOCAL_AUTHORITY_CODE                                                           
E06000001                                                  73296        5698   
E06000002                                                 108161        9431   
E06000003                                                 109763        7553   

                      Age_5_to_9  Age_10_to_14  Age_15_to_19  Age_20_to_24  \
LOCAL_AUTHORITY_CODE                                                         
E06000001                   5192          5653          6278          5955   
E06000002                   8276          8485         10064         11690   
E06000003                   7098          7803          8835          8092   

                      Age_25_to_29  Age_30_to_44  Age_45_to_59  Age_60_to_64  \
LOCAL_AUTHORITY_CODE                                                           
E06000001                     5622         16869         19326          5837   
E06000002                     9765         25414         27065          7531   
E06000003                     7628         24120         28285          9511   

                      Age_65_to_74  Age_75_to_84  Age_85_to_89  \
LOCAL_AUTHORITY_CODE                                             
E06000001                     8174          5568          1323   
E06000002                    10833          7393          1658   
E06000003                    14418          8721          2133   

                      Age_90_and_over  White_British_and_Irish  \
LOCAL_AUTHORITY_CODE                                             
E06000001                         533                    89117   
E06000002                         807                   119680   
E06000003                         980                   132343   

                      White_Other_White  Mixed_or_multiple_ethnic_group  \
LOCAL_AUTHORITY_CODE                                                      
E06000001                           782                             550   
E06000002                          2375                            2362   
E06000003                           860                             853   

                      Asian_or_Asian_British_Indian  \
LOCAL_AUTHORITY_CODE                                  
E06000001                                       266   
E06000002                                      1477   
E06000003                                        91   

                      Asian_or_Asian_British_Pakistani  \
LOCAL_AUTHORITY_CODE                                     
E06000001                                          291   
E06000002                                         6811   
E06000003                                          295   

                      Asian_or_Asian_British_Bangladeshi  \
LOCAL_AUTHORITY_CODE                                       
E06000001                                            214   
E06000002                                            244   
E06000003            

In [11]:
# add new columns by dividing features by total population
grouped = grouped.assign(young_adults = (grouped["Age_20_to_24"] + grouped["Age_25_to_29"] + grouped["Age_30_to_44"]) /grouped["Total_Population"] 
                        ,white = grouped["White_British_and_Irish"] /grouped["Total_Population"] 
                        ,christian = grouped["Christian"] /grouped["Total_Population"] 
                        ,english_speaking = grouped["Main_language_is_English_or_Main_language_not_English__Can_speak_English_very_well"] /grouped["Total_Population"]
                        ,single_ethnicity_household = grouped["All_household_members_have_the_same_ethnic_group"] /grouped["Total_Population"]
                        ,own_home = grouped["Owned_and_Shared_Ownership"]/grouped["Total_Population"]
                        ,not_good_health = (grouped["Fair_health"] + grouped["Bad_health"] + grouped["Very_bad_health"]) /grouped["Total_Population"]
                        ,degree_educated = grouped["Highest_level_of_qualification_Level_4_qualifications_and_above"] /(grouped["Highest_level_of_qualification_Level_4_qualifications_and_above"]+grouped["Highest_level_of_qualification_Level_3_qualifications"]+grouped["Highest_level_of_qualification_Level_1_Level_2_or_Apprenticeship"]+grouped["No_qualifications"])                        
                        ,no_car = grouped["No_cars_or_vans_in_household"] /grouped["Total_Households"]
                        ,private_transport_to_work = grouped["Private_Transport"]/ grouped["Total_Employment_16_to_74"]
                        ,professionals = (grouped["Managers_directors_and_senior_officials"] + grouped["Professional_occupations"]) /grouped["Total_Employment_16_to_74"])

In [12]:
# slice the data frame only for the features that are gonna be used
grouped = grouped.iloc[:,[0,74,75,76,77,78,79,80,81,82,83,84]]

In [13]:
grouped.head(3)

Total_Population  young_adults     white  christian  \
LOCAL_AUTHORITY_CODE                                                        
E06000001                        92028      0.309102  0.968368   0.699233   
E06000002                       138412      0.338619  0.864665   0.632250   
E06000003                       135177      0.294725  0.979035   0.703603   

                      english_speaking  single_ethnicity_household  own_home  \
LOCAL_AUTHORITY_CODE                                                           
E06000001                     0.954297                    0.284935  0.265071   
E06000002                     0.922998                    0.260844  0.238845   
E06000003                     0.962664                    0.292261  0.295620   

                      not_good_health  degree_educated    no_car  \
LOCAL_AUTHORITY_CODE                                               
E06000001                    0.240090         0.183412  0.352871   
E06000002                    0.218637         0.195280  0.375645   
E06000003                    0.237082         0.196985  0.284120   

                      private_transport_to_work  professionals  
LOCAL_AUTHORITY_CODE                                            
E06000001                              0.721927       0.210660  
E06000002                              0.686564       0.204063  
E06000003                              0.749406       0.209213

### Combining referendum results, census data and spatial data

The final part of the preparation is to load the shapefile that contains the geometry needed to draw our maps. This is done using geopandas, which creates a dataframe with spatial data.
We again use the merge function from pandas to merge everything together, but this time we specify the columns to match. We complete the preparation by setting up two additional variables: the difference between leave and remain in local authorities and population density, which might also be an explanatory variable for the vote.

In [14]:
gb = gpd.read_file("shapefiles/boundaries_gb.shp")

In [15]:
gb.head(3)

geo_labelw        geo_label   geo_code          AREA      PERIMETER  \
0       None   South Ayrshire  S12000028  1.222498e+09  271424.465207   
1       None  Huntingdonshire  E07000011  9.129696e+08  207912.519811   
2       None       Tewkesbury  E07000083  4.146167e+08  183303.084764   

                                            geometry  
0  POLYGON ((243296.000 588978.200, 242159.500 58...  
1  POLYGON ((507472.314 299057.906, 511995.531 29...  
2  POLYGON ((381509.283 230085.397, 385473.094 23...

In [16]:
gb.crs = "epsg:27700"

In [17]:
gb.head(3)

geo_labelw        geo_label   geo_code          AREA      PERIMETER  \
0       None   South Ayrshire  S12000028  1.222498e+09  271424.465207   
1       None  Huntingdonshire  E07000011  9.129696e+08  207912.519811   
2       None       Tewkesbury  E07000083  4.146167e+08  183303.084764   

                                            geometry  
0  POLYGON ((243296.000 588978.200, 242159.500 58...  
1  POLYGON ((507472.314 299057.906, 511995.531 29...  
2  POLYGON ((381509.283 230085.397, 385473.094 23...

In [18]:
# change E41000052 value in geo_code column with E06000052
gb.loc[gb["geo_code"] == "E41000052", 'geo_code'] = "E06000052"

# change E41000324 value in geo_code column with E09000033
gb.loc[gb["geo_code"] == "E41000324", 'geo_code'] = "E09000033"

In [19]:
# merge referandum data frame to gb data frame
gb_boundaries = pd.merge(gb, referendum_data, left_on = 'geo_code', right_on = 'Area_Code', how = 'inner')

In [20]:
gb_boundaries.head(3)

geo_labelw        geo_label   geo_code          AREA      PERIMETER  \
0       None   South Ayrshire  S12000028  1.222498e+09  271424.465207   
1       None  Huntingdonshire  E07000011  9.129696e+08  207912.519811   
2       None       Tewkesbury  E07000083  4.146167e+08  183303.084764   

                                            geometry Region_Code      Region  \
0  POLYGON ((243296.000 588978.200, 242159.500 58...   S92000003    Scotland   
1  POLYGON ((507472.314 299057.906, 511995.531 29...   E12000006        East   
2  POLYGON ((381509.283 230085.397, 385473.094 23...   E12000009  South West   

   Area_Code             Area  Electorate  Turnout  Valid_Votes   Leave  
0  S12000028   South Ayrshire       88116   0.6984        61506  0.4104  
1  E07000011  Huntingdonshire      128486   0.7782        99927  0.5424  
2  E07000083       Tewkesbury       67831   0.7915        53652  0.5325

In [21]:
# merge grouped data frame (census + lookup) - all data is in 1 data frame
gb_boundaries = pd.merge(gb_boundaries, grouped, left_on = 'geo_code', right_on = 'LOCAL_AUTHORITY_CODE', how = 'inner')

In [22]:
gb_boundaries.head(2)

geo_labelw        geo_label   geo_code          AREA      PERIMETER  \
0       None   South Ayrshire  S12000028  1.222498e+09  271424.465207   
1       None  Huntingdonshire  E07000011  9.129696e+08  207912.519811   

                                            geometry Region_Code    Region  \
0  POLYGON ((243296.000 588978.200, 242159.500 58...   S92000003  Scotland   
1  POLYGON ((507472.314 299057.906, 511995.531 29...   E12000006      East   

   Area_Code             Area  Electorate  Turnout  Valid_Votes   Leave  \
0  S12000028   South Ayrshire       88116   0.6984        61506  0.4104   
1  E07000011  Huntingdonshire      128486   0.7782        99927  0.5424   

   Total_Population  young_adults     white  christian  english_speaking  \
0            112799      0.278690  0.973466   0.584260          0.879290   
1            169508      0.322427  0.901574   0.608054          0.941183   

   single_ethnicity_household  own_home  not_good_health  degree_educated  \
0                    0.258415  0.313974         0.190418         0.251485   
1                    0.276011  0.294417         0.155527         0.294213   

     no_car  private_transport_to_work  professionals  
0  0.260324                   0.646790       0.254784  
1  0.136169                   0.738221       0.292187

In [23]:
# create two new columsns: leave_remain and pop density
gb_boundaries = gb_boundaries.assign(leave_remain = gb_boundaries["Leave"] - 0.5
                                     ,pop_density = gb_boundaries["Total_Population"] /gb_boundaries["AREA"])

In [24]:
gb_boundaries.head(2)

geo_labelw        geo_label   geo_code          AREA      PERIMETER  \
0       None   South Ayrshire  S12000028  1.222498e+09  271424.465207   
1       None  Huntingdonshire  E07000011  9.129696e+08  207912.519811   

                                            geometry Region_Code    Region  \
0  POLYGON ((243296.000 588978.200, 242159.500 58...   S92000003  Scotland   
1  POLYGON ((507472.314 299057.906, 511995.531 29...   E12000006      East   

   Area_Code             Area  Electorate  Turnout  Valid_Votes   Leave  \
0  S12000028   South Ayrshire       88116   0.6984        61506  0.4104   
1  E07000011  Huntingdonshire      128486   0.7782        99927  0.5424   

   Total_Population  young_adults     white  christian  english_speaking  \
0            112799      0.278690  0.973466   0.584260          0.879290   
1            169508      0.322427  0.901574   0.608054          0.941183   

   single_ethnicity_household  own_home  not_good_health  degree_educated  \
0                    0.258415  0.313974         0.190418         0.251485   
1                    0.276011  0.294417         0.155527         0.294213   

     no_car  private_transport_to_work  professionals  leave_remain  \
0  0.260324                   0.646790       0.254784       -0.0896   
1  0.136169                   0.738221       0.292187        0.0424   

   pop_density  
0     0.000092  
1     0.000186

> **<font color='red'>GROUP DISCUSSION POINT 1</font>**
> 
> Discuss the data in your groups
> 
> * The area census and referendum data reported at different scales. How many geographical areas are each reported in? How are they combined?
> * How are the spatial data combined?
> * What is epsg:27700?
> * Why do you think we are doing `gb.loc[gb["geo_code"]=="E41000052",'geo_code'] = "E06000052"`


### Exploring spatial variation in the Leave:Remain vote

We first observe how voting preference – % share of Leave vote in GB LAs – varies geographically by plotting the raw scores on a map.

The code block below creates a Choropleth map of voting preference by local authority in Great Britain. We convert the geopandas dataframe to a format called *geojson*, which is compatible with the Altair visualisation library. A diverging colour scheme is used to differentiate between majority Leave:Remain, where brown areas have a remain majority and blue areas have a leave majority. 

In [25]:
data_geo = alt.InlineData(values = gb_boundaries.to_json(), # geopandas to geojson string
                          format = alt.DataFormat(property = 'features', type = 'json')
                         )

The conversion into geojson splits columns of the dataframe into geographical column *features* and all other variables under *properties*, which are referenced below. In Altair, we need to specify the type of data for a column, much like we talked about in the first few weeks. The notation below uses the abbreviated version, in which we declare the type of the variable by a single letter after a colon: **N** for nominal, **O** for ordinal, **Q** for quantitative.

In [26]:
alt.Chart(data_geo).mark_geoshape(strokeWidth = 1,
                                  stroke = 'lightgray',
                                  strokeOpacity = 0.2
                                 ).encode(color = alt.Color('properties.leave_remain:Q', 
                                                            scale = alt.Scale(scheme = 'brownbluegreen')),
                                                            tooltip = ['properties.Area:N', 'properties.leave_remain:Q', 'properties.Region:N']
                                                           ).properties(projection = {'type': 'identity','reflectY': True},
                                                                        width = 400,
                                                                        height = 600
                                                                       )

alt.Chart(...)

It is sometimes difficult to see the colours in smaller areas in choropleth maps, so we can filter the data before plotting and have a closer look at particular regions to understand better what is going on.

In [27]:
filtered_geo = alt.InlineData(values = gb_boundaries[gb_boundaries['Region'] == 'South West'].to_json(),
                              format = alt.DataFormat(property = 'features', type = 'json'))

alt.Chart(filtered_geo).mark_geoshape(strokeWidth = 1, 
                                      stroke = 'lightgray', 
                                      strokeOpacity = 0.2
                                     ).encode(color = alt.Color('properties.leave_remain:Q', 
                                                                scale = alt.Scale(scheme = 'brownbluegreen')),
                                                                tooltip=['properties.Area:N', 'properties.leave_remain:Q']
                                                               ).properties(projection={'type': 'identity', 'reflectY': True},
                                                                            width = 400,
                                                                            height = 300
                                                                           )

alt.Chart(...)

> **<font color='red'>GROUP DISCUSSION POINT 2</font>**
> 
>Despite seeing various iterations of these maps in the weeks after the referendum, the very obvious contrast between most of England and Wales (Leave) and Scotland and London, certain University cities and towns (Remain) is surprising. Notice the spot of dark brown in the East of England representing Cambridge.
>
> Discuss the patterns in your groups (though I realise that those who live in UK will have more contextual knowledge).
> 
> * To what extent are these patterns associated with characteristics of the underlying population? Try plotting choropleth maps of some of the variables that we investigate in the next section (e.g. own_home)
> * Can you come up with hypotheses as to why some areas voted the way they did?


## What drives Local Authority voting preference?

As we know, the 48:52 Remain:Leave vote was not the case everywhere. A caricature in the media is of Leave voting being a symptom of blue collar disaffection and Remain voting of liberal values and (relative) affluence. We hope to investigate these ideas in our modelling and identify 2011 Census variables, aggregated to the LA level, that we assume are discriminating:

| complexity | justification/theory |
|:--------------------:|:----------------:|
| *degree-educated* |                               |
| *professional occupations* | post-industrial / knowlegde economy |
| *younger adults* | |
|--------------------|----------------|
| *English speaking* | |
| *single-ethnicity* | |
| *not good health* | diversity / values |
| *white British/Irish* | |
| *Christian* | |
|--------------------|----------------|
| *own home*  | |
| *don't own car* | metropolitan / urban-rural / outcomes |
| *private transport to work* | |

To explore these variables' effect on voting preference, we can create a set of scatter plots that display relationships between each explanatory variable and our outcome. Note that we size the points in the scatter plots by their electoral size and colour by Region. 

In [28]:
# Useful list of variables that we are using in the analysis
variables_to_compare =  ['young_adults', 'white',
                         'christian', 'english_speaking', 'single_ethnicity_household',
                         'own_home', 'not_good_health', 'degree_educated', 'no_car',
                         'private_transport_to_work', 'professionals']

In [29]:
# look at the data that we are gonna visualise in the following steps
gb_boundaries.iloc[:, 6:].head(3)

Region_Code      Region  Area_Code             Area  Electorate  Turnout  \
0   S92000003    Scotland  S12000028   South Ayrshire       88116   0.6984   
1   E12000006        East  E07000011  Huntingdonshire      128486   0.7782   
2   E12000009  South West  E07000083       Tewkesbury       67831   0.7915   

   Valid_Votes   Leave  Total_Population  young_adults     white  christian  \
0        61506  0.4104            112799      0.278690  0.973466   0.584260   
1        99927  0.5424            169508      0.322427  0.901574   0.608054   
2        53652  0.5325             81943      0.293997  0.945657   0.665731   

   english_speaking  single_ethnicity_household  own_home  not_good_health  \
0          0.879290                    0.258415  0.313974         0.190418   
1          0.941183                    0.276011  0.294417         0.155527   
2          0.954481                    0.286589  0.319417         0.167482   

   degree_educated    no_car  private_transport_to_work  professionals  \
0         0.251485  0.260324                   0.646790       0.254784   
1         0.294213  0.136169                   0.738221       0.292187   
2         0.314578  0.135939                   0.742008       0.287984   

   leave_remain  pop_density  
0       -0.0896     0.000092  
1        0.0424     0.000186  
2        0.0325     0.000198

The code below defines a single scatterplot. As we want to define multiple scatterplots, we need to use a composition method. In Altair, we can do that using *repeat*. This requires us first to define a list of variables that we will iterate through (we will use the variable specified above). We then need to refer back to this list in the visual variables that we want to vary. In this case, as we want different variables in the horizontal (X) axis, that's where we place a special variable called alt.repeat().

In [30]:
base_scatter = alt.Chart(gb_boundaries.iloc[:, 6:]
                        ).mark_circle(strokeWidth = 1, stroke = 'black', strokeOpacity = 0.2
                                     ).encode(x = alt.X('young_adults:Q', scale = alt.Scale(domain = [0.2, 0.6])),
                                              y = alt.X('Leave:Q', scale = alt.Scale(domain = [0.15, 0.8])),
                                              size = 'Electorate:Q',
                                              color = alt.Color('leave_remain:Q', scale = alt.Scale(scheme = 'brownbluegreen')),
                                              tooltip = ['Region:N','Area:N']
                                             ).properties(width = 1000,
                                                          height = 500)
base_scatter

alt.Chart(...)

Compare the code below with the code above. Below we modify how we map a data variable to a visual variable, include some helper functions to define the scale of the vertical axis for every scatterplot (the *domain*), include the repeat function to generate multiple scatterplots and tell Altair how we want it to specify the scales for each scatterplot (*independently*).

To experiment with the visualisation, we can, for example, modify *resolve_scale*, switching from *independent* to *shared*, and see how each scatterplot looks afterwards.

In [31]:
alt.Chart(gb_boundaries.iloc[:, 6:]).mark_circle(strokeWidth = 1, stroke = 'black', strokeOpacity = 0.2
                                                ).encode(x = alt.X(alt.repeat(), type = 'quantitative'),
                                                         y = alt.Y('Leave:Q', scale = alt.Scale(domain = [0.15, 0.8])),
                                                         size = 'Electorate:Q',
                                                         color = alt.Color('leave_remain:Q', scale = alt.Scale(scheme = 'brownbluegreen')),
                                                         tooltip = ['Region:N', 'Area:N']
                                                        ).properties(width = 250,
                                                                     height = 125
                                                                    ).repeat(variables_to_compare,
                                                                             columns = 4
                                                                            ).resolve_scale(x = 'independent', y = 'independent')

alt.RepeatChart(...)

Altair also allows us to add interactive widgets and attach them to the visualisations. Below there is an example of the same series of scatterplots, with an additional dropdown that enables us to filter the scatterplot by region.

Take some time to understand the code and also read the [documentation](https://altair-viz.github.io/user_guide/interactions.html) if you want to know more about interactions with Altair. Note that due to the behaviour of the library we're using a workaround to filter the nodes: instead of removing them from view, we modify their opacity. This means that, when you hover the mouse, you will see that there are tooltips for invisible circles. If data points were actually removed from view, Altair would recalculate the colours and circle sizes, making it more difficult to compare the regions each time we selected a different one. Our *design choice* here is to preserve colour and size and tolerate the tooltips for invisible circles.

In [32]:
input_dropdown = alt.binding_select(options = gb_boundaries.Region.unique().tolist())
selection = alt.selection_single(fields = ['Region'], bind = input_dropdown, name = 'Select')
opacity = alt.condition(selection, alt.value(1), alt.value(0)) # this tells Altair to set opacity to 1 (fully visible) for the selected 

alt.Chart(gb_boundaries.iloc[:, 6:]).mark_circle(strokeWidth = 1, stroke = 'black', strokeOpacity = 0.2
                                                ).encode(x = alt.X(alt.repeat(), type = 'quantitative'),
                                                         y = alt.Y('Leave:Q', scale = alt.Scale(domain = [0.15, 0.8])),
                                                         size = 'Electorate:Q',
                                                         color = alt.Color('leave_remain:Q', scale = alt.Scale(scheme = 'brownbluegreen')),
                                                         opacity = opacity,
                                                         tooltip = ['Region:N', 'Area:N', 'Leave:Q']
                                                        ).properties(width = 250,
                                                                     height = 125
                                                                    ).add_selection(selection
                                                                                   ).repeat(variables_to_compare,
                                                                                            columns = 4
                                                                                           ).resolve_scale(x = 'independent', y = 'independent'
                                                                                                          )

alt.RepeatChart(...)

In [33]:
alt.Chart(gb_boundaries.iloc[:, 6:]).mark_circle(strokeWidth = 1, stroke = 'black', strokeOpacity = 0.2
                                                ).encode(x = alt.X(alt.repeat(), type = 'quantitative'),
                                                         y = alt.Y('Leave:Q', scale = alt.Scale(domain = [0.15, 0.8])),
                                                         size = 'Electorate:Q',
                                                         color = alt.Color('Region:N', scale = alt.Scale(scheme = 'set3')),  # here is where we change the colour
                                                         tooltip = ['Region:N', 'Area:N', 'Leave:Q']
                                                        ).properties(width = 250,
                                                                     height = 125,
                                                                    ).repeat(variables_to_compare,
                                                                             columns = 4
                                                                            ).resolve_scale(x = 'independent', y = 'independent'
                                                                                          )

alt.RepeatChart(...)

> **<font color='red'>GROUP DISCUSSION POINT 3</font>**
>
> * Which variables seems to most correspond to likliness of voting leave?
> * Any suggestions of why? (Do some causal thinking!)
> * Do there seem to be regional differences?

## Assumptions of linear regression and the case for local model(s)

Now we've found some variables that not only correlate with the share of Remain:Leave vote but also correspond to phenomena that might help explain the vote. We can try to build models to take account of the effects of these variables on the vote.

We will generate a multivariate regression model using the variables above that we hypothesise are discriminating. It's worth here quickly revisiting the assumptions of multivariate linear regression:

* Linear relationship between expected value of outcome and each explanatory variable
* No or limited collinearity of explanatory variables
* No (spatial) auto-correlation in residuals 
* Homoscedasticity (constant variance) in residuals
* Normality in distribution of residuals

We have already identified linearity in the relationships between our outcome and candidate explanatory variables and we'll discuss the distribution of model residuals shortly. However, we've yet to address the problem of collinearity of explanatory variables. Since we wish to develop a model for *explaining* voter preference, it's important that our model is parsimonious: that is, that we can explain the outcome with as few explanatory variables as possible. **Attending to issues of collinearity helps us to do this: we can eliminate variables that effectively represent the same concept.**

**Collinearity can initially be assessed through studying pairwise correlation between each explanatory variable** -- the code below allows a matrix of pairwise correlation coefficients to be generated. 

In [34]:
model_variables = ['Leave', 'young_adults', 'white',
                   'christian', 'english_speaking', 'single_ethnicity_household',
                   'own_home', 'not_good_health', 'degree_educated', 'no_car',
                   'private_transport_to_work', 'professionals','pop_density']

In [35]:
corr_matrix = pd.melt(gb_boundaries[model_variables].corr(method = 'pearson').reset_index(), id_vars = ['index'])

In [36]:
corr_matrix.head()

index variable     value
0             Leave    Leave  1.000000
1      young_adults    Leave -0.452986
2             white    Leave  0.404088
3         christian    Leave  0.494341
4  english_speaking    Leave  0.491394

In [37]:
# create base chart
base = alt.Chart(corr_matrix).encode(x = alt.X('index:N', scale = alt.Scale(paddingInner = 0), sort = alt.EncodingSortField('index', order = 'ascending')),
                                     y = alt.Y('variable:N', scale = alt.Scale(paddingInner = 0), sort = alt.EncodingSortField('index', order = 'ascending')),
                                    )
# create heatmap
heatmap = base.mark_rect().encode(color = alt.Color('value:Q', scale = alt.Scale(domain = [-1,1], scheme = 'redblue')),
                                  tooltip=['value', 'index', 'variable']
                                 )
# create text
text = base.mark_text(baseline = 'middle').encode(alt.Text('value', format = '.2f'),
                                                  color = alt.value('white'),
                                                  tooltip = ['value', 'index', 'variable']
                                                 )
# combine
(heatmap + text).properties(width = 500, height = 500).configure_axis(title = None)

alt.LayerChart(...)

(Note how the code above takes a slightly different approach to create the charts, demonstrating the flexibility of *declarative* visualisation grammars. We first define a *skeleton* chart, defining only the X and Y variables we want to use, and assign it to variable *base*. We extend this base twice: to specify the heatmap itself and then to add the text labels. We then use the [layer operator](https://altair-viz.github.io/user_guide/compound_charts.html) from Altair, +, to combine the two charts.)

**An established technique for identifying problems of collinearity within a multiple regression model itself is the [Variance Inflation Factor](https://en.wikipedia.org/wiki/Variance_inflation_factor) (VIF).** VIF measures how much the __variance__ of the estimated regression coefficients are inflated as compared to when the explanatory variables are *not* linearly related. There are heuristics around the level of collinearity that can be tolerated for each variable: VIF values of 2-5 represent reasonably low levels of variance inflation due to collinearity and VIF >= 10 represent a tolerance threshold that should be avoided. A reasonable method for inclusion or exclusion of explanatory variables might be to:

* identify variables that appear to be discriminating (based on the strength of correlation against the outcome).
* identify variables which appear to co-vary *and* which are conceptually similar -- ***degree_educated*** and ***professionals*** would be the most obvious initial pair.
* explore the effect of removing the explanatory variable on VIF scores and model fit.

In this study we wish to develop a model for *understanding* spatial variations in voting preference. That the explanatory variables we use also represent separate concepts, and are few in number (so the model can be easily understood), is important. We don't in this practical detail in full the decision making process (there's already plenty to read!). However, the multivariate model we specify based on this process is:

`Leave ~ younger_adults + christian + english_speaking + degree_educated + white + no_car`

(This formula is based on a traditional notation that originates in R and is compatible with many libraries for statistical modelling. You can see more details about it [here](https://faculty.chicagobooth.edu/richard.hahn/teaching/formulanotation.pdf))

In your coursework projects we expect this decision-making to be made transparent. As well as making data-driven decisions (e.g. using correlation coefficients and VIF scores in this case), we'd expect a justification grounded in your data analysis context. 

Below we use code to join our list of variables together, so that we can have a dynamic way to try different models. You can do that by slicing the selected_variables array, or removing values and re-running the cell.

In [38]:
selected_variables =  ['Leave','young_adults', 'white',
                       'christian', 'english_speaking', 'single_ethnicity_household',
                       'own_home', 'not_good_health', 'degree_educated', 'no_car',
                       'private_transport_to_work', 'professionals','pop_density']

In [39]:
# define model variables in a abovementioned format
str_model_variables = ' + '.join(selected_variables[1:]) # note that we use :1 to remove Leave from the list, as it is the dependent variable

In [40]:
str_model_variables

'young_adults + white + christian + english_speaking + single_ethnicity_household + own_home + not_good_health + degree_educated + no_car + private_transport_to_work + professionals + pop_density'

In [41]:
# create the model
lm = smf.ols(formula = 'Leave ~ ' + str_model_variables, data = gb_boundaries).fit()

In [42]:
lm

In [43]:
print(lm.summary())

                            OLS Regression Results                            
Dep. Variable:                  Leave   R-squared:                       0.858
Model:                            OLS   Adj. R-squared:                  0.854
Method:                 Least Squares   F-statistic:                     184.1
Date:                Thu, 02 Dec 2021   Prob (F-statistic):          1.32e-146
Time:                        19:56:56   Log-Likelihood:                 691.49
No. Observations:                 378   AIC:                            -1357.
Df Residuals:                     365   BIC:                            -1306.
Df Model:                          12                                         
Covariance Type:            nonrobust                                         
                                 coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------------
Intercept           

In [44]:
variables = lm.model.exog

In [45]:
vif = [variance_inflation_factor(variables, i) for i in range(variables.shape[1])]

In [46]:
display(Markdown('**Variance Inflation Factors**'))
print("---")
for i in range(len(selected_variables[1:])):
    display(Markdown('**' + selected_variables[i + 1] + '**: ' + str(vif[i + 1].round(1)))) # ** markdown for bold
print("---")

**Variance Inflation Factors**

---


**young_adults**: 8.8

**white**: 10.0

**christian**: 2.7

...

**no_car**: 16.7

**private_transport_to_work**: 10.0

**professionals**: 16.8

**pop_density**: 8.0

---


### Exposing regional variation

A case can be made for local (or geographically-weighted) regression where there is spatial dependency in model residuals. Remembering that residuals are the difference between an observed outcome and that outcome estimated by the linear model, spatial clustering of, for instance, negative residuals -- where the model predicts a lower Leave vote than expected given socio-economic context -- suggests there is something particular about that local context. 

In [47]:
results_degree = smf.ols(formula = 'Leave ~ degree_educated', data = gb_boundaries).fit()

results_refined = smf.ols(formula = '''Leave ~ young_adults + christian + english_speaking + professionals + white + no_car''', data = gb_boundaries).fit()

gb_boundaries = gb_boundaries.assign(resids_degree = results_degree.resid)
gb_boundaries = gb_boundaries.assign(resids_refined = results_refined.resid)

In [48]:
alt.Chart(alt.InlineData(values = gb_boundaries.to_json(),
                         format = alt.DataFormat(property = 'features', type = 'json'))
         ).mark_geoshape(strokeWidth = 1, stroke = 'lightgray', strokeOpacity = 0.2
                        ).encode(color = alt.Color(alt.repeat('column'), type = 'quantitative', scale = alt.Scale(scheme = 'redblue')),
                                 tooltip = ['properties.Area:N', alt.Tooltip(alt.repeat("column"), type = "quantitative")]
                                ).properties(projection = {'type': 'identity', 'reflectY': True},
                                             width = 500,
                                             height = 500
                                            ).repeat(column = ['properties.resids_degree', 'properties.resids_refined'])

alt.RepeatChart(...)

> **<font color='red'>GROUP DISCUSSION POINT 4</font>**
>
> Note that these are residual maps. White means the model predicts correctly, **blue underestimates % leave, red overestimates % leave**.
>
> * Comment on the two models. Why does is the "Scottish effect" less marked in the second model?
> * To what extent is there geographical variation?
> * If you can, explore other combinations of variables and study the model fits, VIF scores and correlations in conjunction with the maps.

## Exploring spatially-varying relationships using geographically-weighted statistics

We finish the practical by exploring whether and how relationships between our selected explanatory variables vary spatially using geographically-weighted (gw) statistics.

You will recall from the lecture that gw-statistics enable spatial variations in values, distributions and relationships between variables to be explored by generating local *models* (broadly defined) at each observation area -- each LA in this case. The technique involves a moving spatial window and weighting scheme such that nearby locations are given greater salience in the model. 

We'll generate gw-summary statistics by first fitting a model, then evaluating the results. The purpose here is to support understanding of how correlations between our outcome and explanatory variable change over space. And we'll inspect these correlation coefficient values by plotting them in Choropleth maps.

In [49]:
# GWR below requires the "centroids" of each geographical area
centroids = np.array([[c.x, c.y] for c in gb_boundaries.geometry.centroid])

#These are all the variables we want to apply geographically-weighted statistics
refined_vars = ["young_adults", "white" , "christian", "english_speaking", 
                "single_ethnicity_household", "own_home", "not_good_health", "degree_educated", "no_car", 
                "private_transport_to_work", "professionals"]

coeff_names = ['intercept']
map_vars = []

for var in refined_vars:
    coeff_names.append('coeff_' + var)
    map_vars.append('properties.coeff_' + var)

In [50]:
# Define GWR model
model = GWR(centroids,gb_boundaries['Leave'].to_numpy().reshape((-1, 1)),
            gb_boundaries[refined_vars].to_numpy(),
            bw = 50,
            kernel = 'bisquare',
            fixed = False)

gw_results = model.fit()

In [51]:
# GWR or GWRResult does not calculate geographically-weighted correlation coefficients for all variables
# So, this is an adapted version of https://github.com/pysal/mgwr/blob/master/mgwr/gwr.py#L1092
def all_corr(results,variables):
    """
    Computes  local correlation coefficients (n, (((p+1)**2) + (p+1) / 2) within a geographically
    weighted design matrix
    Returns one array with the order and dimensions listed above where n
    is the number of locations used as calibrations points and p is the
    number of explanatory variables; +1 accounts for the dependent variable.
    Local correlation coefficient is not calculated for constant term.
    """
    #print(self.model)
    x = results.X
    y = results.y
    x = np.column_stack((x,y))
    w = results.W
    nvar = x.shape[1]
    nrow = len(w)
    if results.model.constant:
        ncor = (((nvar - 1)**2 + (nvar - 1)) / 2) - (nvar - 1)
        jk = list(combo(range(1, nvar), 2))
    else:
        ncor = (((nvar)**2 + (nvar)) / 2) - nvar
        jk = list(combo(range(nvar), 2))
    corr_mat = np.ndarray((nrow, int(ncor)),dtype=dict)
    
    for i in range(nrow):
        wi = w[i]
        sw = np.sum(wi)
        wi = wi / sw
        tag = 0

        for j, k in jk:
            val = corr(np.cov(x[:, j], x[:, k], aweights=wi))[0][1] 
            corr_mat[i,tag] = {"var": variables[j-1]+"_"+variables[k-1], "var_1": variables[j-1], "var_2": variables[k-1], "value": val}
            tag = tag + 1
            
    return corr_mat

In [52]:
corr_matrix = all_corr(gw_results, refined_vars + ['Leave'])

# Filter only those correlation coefficients against the Leave vote
corr_2 = [{d['var']: d['value'] for d in x if d['var_2'] == 'Leave'} for x in corr_matrix]

corr_coeffs = pd.DataFrame.from_records(corr_2)

In [53]:
# Check if we have what we wanted (all variables correlated with Leave)
corr_coeffs.head()

young_adults_Leave  white_Leave  christian_Leave  english_speaking_Leave  \
0           -0.272977     0.448262         0.488468                0.633269   
1           -0.489447     0.281828         0.562300               -0.077148   
2           -0.263900     0.095990         0.379267                0.006428   
3           -0.314278     0.185083         0.070528                0.085439   
4           -0.085391     0.168854         0.264475                0.069085   

   single_ethnicity_household_Leave  own_home_Leave  not_good_health_Leave  \
0                          0.707520        0.087977               0.545547   
1                          0.654490        0.437352               0.842521   
2                          0.433343        0.194651               0.734683   
3                          0.431903        0.331045               0.389133   
4                          0.224415       -0.151247               0.657184   

   degree_educated_Leave  no_car_Leave  private_transport_to_work_Leave  \
0              -0.443554     -0.247502                         0.545193   
1              -0.969710     -0.147410                         0.789762   
2              -0.887069      0.049972                         0.659010   
3              -0.530288     -0.202253                         0.576025   
4              -0.839289      0.377051                         0.564091   

   professionals_Leave  
0            -0.525329  
1            -0.936784  
2            -0.778870  
3            -0.442164  
4            -0.799127

In [54]:
corr_df = pd.merge(gb_boundaries, corr_coeffs, left_index = True,right_index = True)

map_vars = ['properties.' + v for v in corr_coeffs.columns.values ]

corr_geo = alt.InlineData(values = corr_df.to_json(),
                          format = alt.DataFormat(property = 'features', type = 'json'))

In [55]:
print(corr_coeffs.columns.values)

alt.Chart(corr_geo).mark_geoshape(strokeWidth = 1, stroke = 'lightgray', strokeOpacity = 0.2
                                 ).encode(color = alt.Color(alt.repeat('repeat'), type = 'quantitative', scale = alt.Scale(scheme = 'purplegreen')),
                                          tooltip = ['properties.Area:N', alt.Tooltip(alt.repeat("repeat"), type="quantitative")]
                                         ).properties(projection = {'type':'identity', 'reflectY': True},
                                                      width = 200,
                                                      height = 300,
                                                     ).repeat(map_vars, columns = 4)

['young_adults_Leave' 'white_Leave' 'christian_Leave'
 'english_speaking_Leave' 'single_ethnicity_household_Leave'
 'own_home_Leave' 'not_good_health_Leave' 'degree_educated_Leave'
 'no_car_Leave' 'private_transport_to_work_Leave' 'professionals_Leave']


alt.RepeatChart(...)

> **<font color='red'>GROUP DISCUSSION POINT 5</font>**
>
> The maps are correlation coefficients for the variables in the order listed above with %leave.
>
> * Study the maps. Which variables are more regionally distinct?
> * Can you offer explanations as to why this might be?


Scanning across the maps and making systematic claims about combinations of relationships is challenging. Clustering LAs on their gw-correlation coefficients might help. In the code below, each LA is summarised according to its geographically-weighted correlation coefficient and agglomerative hierarchical cluster analysis (HCA) is used to identify groups of LAs that share *similar combinations of relationship*. LAs are then ‘agglomerated’ into groups iteratively by merging the most similar LAs. This continues until all LAs are merged into a single group. We can evaluate the clustering visually by plotting a dendrogram depicting this agglomeration process, and numerically by considering Average Silhouette Width (ASW) values, calculated at different cuts (number of clusters) of the dendrogram. 

We won't go into length about the choice of cluster analysis: if two variables are included that represent the same concept, then that concept is given undue weight. Variables were carefully selected by visually inspecting correlation matrices of the geographically-weighted correlation coefficients – similar to the approach for assessing collinearity in regression. The input variables selected via this process are: __Christian, degree-educated, no car, not good health, white.__



In [56]:
# First we standardise the variables
cluster_variables = ['christian_Leave', 'degree_educated_Leave' ,'no_car_Leave','not_good_health_Leave' , 'white_Leave' ]
scaler = StandardScaler()
scaled_coefficients = scaler.fit_transform(corr_coeffs[cluster_variables])
scaled_df = pd.DataFrame(scaled_coefficients, columns = corr_coeffs[cluster_variables].columns)

In [57]:
print('---')
cluster_results = [None] * 12
for i in range(2, 12): 
    ac = AgglomerativeClustering(linkage = 'ward', n_clusters = i)
    cr = ac.fit(scaled_df.values)
    cluster_results[i] = cr
    print(str(i) + " clusters. Avg silhouette score:", silhouette_score(scaled_df.values,cr.labels_))
print('---')

---
2 clusters. Avg silhouette score: 0.32432981144902706
3 clusters. Avg silhouette score: 0.32874922095825526
4 clusters. Avg silhouette score: 0.3093710651622909
5 clusters. Avg silhouette score: 0.317487961047737
6 clusters. Avg silhouette score: 0.30453128132123214
7 clusters. Avg silhouette score: 0.3119976375595494
8 clusters. Avg silhouette score: 0.31823221994747947
9 clusters. Avg silhouette score: 0.3084300411411974
10 clusters. Avg silhouette score: 0.3243508458031119
11 clusters. Avg silhouette score: 0.31986323795181665
---


We can then visually inspect the silhouette scores plot for each solution. By re-running the next three blocks of code for each solution, we will see how there is not a definitive perfect solution. Remember that for each member of a cluster (Local Authorities), a negative value might suggest that the LA is in the wrong cluster. With 4 clusters, cluster 1 only has positive values, but cluster 0 has some really bad silhouette scores. Increasing to 5, we can see that cluster 1 is actually slightly worse, but cluster 0 improves significantly. As our aim here is to understand more the differences between the Leave vote in LA's based on geography and census variables, it is natural that some areas are more difficult to "place" in a single cluster.

At this point, we could also conclude that traditional clustering techniques are not helpful and move towards a "fuzzy" clustering solution: where a Local Authority belongs with different degrees of membership to various clusters. But we leave that for braver data scientists adventurers to explore :)

In [58]:
hc_result = cluster_results[5] 
corr_df['cluster_membership'] = hc_result.labels_
corr_coeffs['cluster_membership'] = hc_result.labels_

corr_coeffs.head(3)

young_adults_Leave  white_Leave  christian_Leave  english_speaking_Leave  \
0           -0.272977     0.448262         0.488468                0.633269   
1           -0.489447     0.281828         0.562300               -0.077148   
2           -0.263900     0.095990         0.379267                0.006428   

   single_ethnicity_household_Leave  own_home_Leave  not_good_health_Leave  \
0                          0.707520        0.087977               0.545547   
1                          0.654490        0.437352               0.842521   
2                          0.433343        0.194651               0.734683   

   degree_educated_Leave  no_car_Leave  private_transport_to_work_Leave  \
0              -0.443554     -0.247502                         0.545193   
1              -0.969710     -0.147410                         0.789762   
2              -0.887069      0.049972                         0.659010   

   professionals_Leave  cluster_membership  
0            -0.525329                   2  
1            -0.936784                   0  
2            -0.778870                   3

In [59]:
sil_scores = pd.DataFrame(np.column_stack((silhouette_samples(scaled_df.values, hc_result.labels_), hc_result.labels_)),
                          columns = ['silhouette', 'cluster_m']).reset_index()

In [60]:
alt.Chart(sil_scores).mark_bar().encode(x = 'silhouette:Q',
                                        y = alt.Y('index:O', sort = alt.SortField(field = "silhouette", order = 'descending'), axis = None),
                                        color = alt.Color('cluster_m:N', scale = alt.Scale(scheme = 'accent')),
                                        facet = 'cluster_m:N'
                                       ).properties(width = 150, height = 250).resolve_scale(y = 'independent')

alt.Chart(...)

Below the cluster memberships are displayed on a choropleth map and described on the variables on which they were defined via density plots. We’ve also come up with cluster labels that try to characterise these distributions. This of course requires knowledge besides that which comes from the census variables; in the individual coursework, it is helpful to choose datasets for which you do have this "extra" knowledge if you intend to add additional *domain* discussions to the analysis.

In [61]:
alt.Chart(alt.InlineData(values = corr_df.to_json(),
                         format = alt.DataFormat(property = 'features', type = 'json')) 
         ).mark_geoshape(strokeWidth = 1, stroke = 'lightgray', strokeOpacity = 0.2
                        ).encode(color = alt.Color('properties.cluster_membership:N', scale = alt.Scale(scheme = 'accent')),
                                 tooltip = ['properties.Area:N', 'properties.cluster_membership:N']
                                ).properties(projection = {'type': 'identity','reflectY': True},
                                             width = 500,
                                             height = 700,
                                            )

alt.Chart(...)

The code below is prepared for 5 clusters, but it is easy to change according to the number of clusters if we wish to test others. The truly hardcoded line is the last one, which assembles the complete chart. But that technically is not necessary. To display cluster groups charts individually, it is enough to write in a code cell `display(chart[i])`

***Note***: There is a [known compatibility issue](https://github.com/altair-viz/altair/issues/2496) between the current versions of Altair and jsonschema leading to errors for the below code. While the issue appears to be fixed, it only will be available with the next release. The current solution is to install an older version of jsonschema (if you use pip: pip install jsonschema==3.2.0).

In [62]:
#Change this (below) for different correlation pairs
corr_pair=corr_coeffs.columns[0]

names = ['Group 1: Economic competitiveness and various others',
         'Group 2: Economic competitiveness and sometimes others', 
         'Group 3: Economic competitiveness and material outcomes',
         'Group 4: Economic competitiveness and values (media caricature)',
         'Group 5: Home counties commuter belt']

charts = []

for i in range(len(names)):

    c1 = alt.Chart(pd.DataFrame([{"x": 0}])).mark_rule().encode(x = alt.X('x:Q'), color = alt.value('lightgray'))
    
    c2 =  alt.Chart(corr_coeffs
            ).transform_filter(
                alt.datum.cluster_membership == i
            ).mark_area(interpolate='monotone',line=True
            ).encode(
                x=alt.X(corr_pair, bin=alt.Bin(extent=[-1.0,1.0],step=0.1),scale=alt.Scale(domain=[-1,1])),    
                y=alt.Y('count()',title=None,scale=alt.Scale(domain=[0,80])),
                color=alt.Color('cluster_membership:O',scale=alt.Scale(scheme='accent'))
            ).properties(width=120,height=100)
    
    chart = (c1+c2
          ).encode(
                x=alt.X(
                        type='quantitative',
                        bin=alt.Bin(extent=[-1.0,1.0],step=0.1),
                        scale=alt.Scale(domain=[-1,1]),
                        axis=alt.Axis(tickCount=4,labelOverlap=False))
          ).resolve_scale(y='shared'
          ).properties(title=names[i])
          
    
    charts.append(chart)
    
(charts[0] & charts[1] & charts[2] & charts[3] & charts[4]).configure(fieldTitle='plain').configure_axis(
    grid=False
)

alt.VConcatChart(...)

> **<font color='red'>GROUP DISCUSSION POINT 6</font>**
>
> * What are the limitations of this study? For example, remember we’re not looking at individual data, we’re using LA-level population data and vote results.
> * What phenomena and concepts are not captured well by our 2011 Census variables?
> * How conclusive is our analysis?

## Further reading

* Bartholomew, D. J., Steele, F., Galbraith, J. & Moustaki, I. (2008), **[Analysis of Multivariate Social Science Data](http://www.lse.ac.uk/statistics/research/Social-Statistics/Multivariate-Data-Analysis/Second-Edition.aspx)**, Second Edition, 2 edn, Chapman and Hall/CRC Press, London.
* Goodwin, M. and Heath, O. (2016), **[The 2016 Referendum, Brexit and the Left Behind: An Aggregate-level Analysis of the Result](http://onlinelibrary.wiley.com/doi/10.1111/1467-923X.12285/full)**, *The Political Quarterly*, 87:323–332.
* Beecham, R., Slingsby, A. and Brunsdon, C. (2018). **[Locally-varying explanations behind the United Kingdom’s vote to the Leave the European Union](http://openaccess.city.ac.uk/id/eprint/19048/)**. *Journal of Spatial Information Science*, 16, pp. 117-136.
